In [64]:
import os
import re

import shutil
import codecs, json 
import nibabel as nib
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import seaborn as sns
import scipy as sp
from scipy import stats
import sklearn as sk
import time
from dypac import Dypac
import nilearn
from nilearn import image, plotting, datasets
from nilearn.input_data import NiftiLabelsMasker, NiftiMasker
from nilearn.connectome import ConnectivityMeasure
from nilearn.decomposition import DictLearning, CanICA
from scipy.stats import pearsonr
import nilearn.plotting as plotting
import math
import hcp_utils as hcp

import conf
import helper_functions
import roi_analysis_func
import importlib

### Load the concatenated files

In [67]:
#All data - in d
dir_name = conf.CONCATENATED_DATA_DIR

#Sample data - in local folder
#dir_name = conf.BASE_DIR + 'RS_data/concatenated_data_sample_preprocessed/'
    
subjects = os.listdir(dir_name)

len(subjects)

992

In [68]:
paths = []
for sub in subjects:
    paths.append(dir_name + '{0}'.format(sub))
data = paths
data

['/mnt/d/HCP_Liz/concatenated_data/100206.npz',
 '/mnt/d/HCP_Liz/concatenated_data/209834.npz',
 '/mnt/d/HCP_Liz/concatenated_data/209935.npz',
 '/mnt/d/HCP_Liz/concatenated_data/250932.npz',
 '/mnt/d/HCP_Liz/concatenated_data/214625.npz',
 '/mnt/d/HCP_Liz/concatenated_data/251833.npz',
 '/mnt/d/HCP_Liz/concatenated_data/214524.npz',
 '/mnt/d/HCP_Liz/concatenated_data/210011.npz',
 '/mnt/d/HCP_Liz/concatenated_data/210112.npz',
 '/mnt/d/HCP_Liz/concatenated_data/214726.npz',
 '/mnt/d/HCP_Liz/concatenated_data/255639.npz',
 '/mnt/d/HCP_Liz/concatenated_data/217126.npz',
 '/mnt/d/HCP_Liz/concatenated_data/210415.npz',
 '/mnt/d/HCP_Liz/concatenated_data/255740.npz',
 '/mnt/d/HCP_Liz/concatenated_data/217429.npz',
 '/mnt/d/HCP_Liz/concatenated_data/210617.npz',
 '/mnt/d/HCP_Liz/concatenated_data/256540.npz',
 '/mnt/d/HCP_Liz/concatenated_data/219231.npz',
 '/mnt/d/HCP_Liz/concatenated_data/211114.npz',
 '/mnt/d/HCP_Liz/concatenated_data/257542.npz',
 '/mnt/d/HCP_Liz/concatenated_data/22072

In [69]:
#Delate the npz ending
subjects_num = []

for i in range(len(subjects)):
    subjects_num.append(subjects[i][:6])

##Convert subject nums from strings to integers
subjects_num = list(map(int, subjects_num))
subjects_num

[100206,
 209834,
 209935,
 250932,
 214625,
 251833,
 214524,
 210011,
 210112,
 214726,
 255639,
 217126,
 210415,
 255740,
 217429,
 210617,
 256540,
 219231,
 211114,
 257542,
 220721,
 211215,
 257845,
 221319,
 211316,
 257946,
 223929,
 211417,
 263436,
 224022,
 211619,
 268850,
 227432,
 211720,
 270332,
 227533,
 211821,
 274542,
 228434,
 211922,
 275645,
 231928,
 212015,
 280739,
 233326,
 212116,
 280941,
 237334,
 212217,
 281135,
 238033,
 212318,
 283543,
 239136,
 212419,
 285345,
 239944,
 212823,
 285446,
 245333,
 213017,
 286347,
 246133,
 213421,
 286650,
 248339,
 213522,
 287248,
 249947,
 214019,
 289555,
 250427,
 214221,
 290136,
 268749,
 214423,
 293748,
 295146,
 322224,
 297655,
 325129,
 298051,
 100307,
 329440,
 298455,
 299154,
 100408,
 330324,
 299760,
 300618,
 100610,
 334635,
 300719,
 303119,
 101006,
 339847,
 303624,
 304020,
 101107,
 342129,
 304727,
 305830,
 101309,
 346945,
 307127,
 308129,
 101915,
 349244,
 308331,
 309636,
 102008,
 

### Load seed (=mask)

In [70]:
file = conf.BASE_DIR + 'ROI_analysis/masks/viz_union_mask.dtseries.nii'

img = nib.load(file)
mask = img.get_fdata()
mask.shape

(1, 91282)

In [71]:
#Validate that is a binary mask
np.unique(mask)

array([0., 1.])

In [72]:
importlib.reload(roi_analysis_func)
idx = roi_analysis_func.idx_mask(mask)
len(idx)

4690

In [73]:
mask.shape[1]

91282

### step 1: create seed2voxel maps

In [74]:
N = len(subjects_num)
num_v = mask.shape[1] #91282

all_seed2voxel = np.empty([num_v, N])

for i,sub in enumerate(data):
    # load subject resting state data
    subject_rs = np.load(data[i])['a']
    # Average the relevant vertices according to the mask (idx)
    roi_ts = subject_rs[:,idx].mean(axis=1)
    for v in range(num_v):
        all_seed2voxel[(v,i)] = pearsonr(subject_rs[:,v], roi_ts)[0]
    print("finished subject {0}".format(i), flush = True)

finished subject 0
finished subject 1
finished subject 2
finished subject 3
finished subject 4
finished subject 5
finished subject 6
finished subject 7
finished subject 8
finished subject 9
finished subject 10
finished subject 11
finished subject 12
finished subject 13
finished subject 14
finished subject 15
finished subject 16
finished subject 17
finished subject 18
finished subject 19
finished subject 20
finished subject 21
finished subject 22
finished subject 23
finished subject 24
finished subject 25
finished subject 26
finished subject 27
finished subject 28
finished subject 29
finished subject 30
finished subject 31
finished subject 32
finished subject 33
finished subject 34
finished subject 35
finished subject 36
finished subject 37
finished subject 38
finished subject 39
finished subject 40
finished subject 41
finished subject 42
finished subject 43
finished subject 44
finished subject 45
finished subject 46
finished subject 47
finished subject 48
finished subject 49
finished s

finished subject 396
finished subject 397
finished subject 398
finished subject 399
finished subject 400
finished subject 401
finished subject 402
finished subject 403
finished subject 404
finished subject 405
finished subject 406
finished subject 407
finished subject 408
finished subject 409
finished subject 410
finished subject 411
finished subject 412
finished subject 413
finished subject 414
finished subject 415
finished subject 416
finished subject 417
finished subject 418
finished subject 419
finished subject 420
finished subject 421
finished subject 422
finished subject 423
finished subject 424
finished subject 425
finished subject 426
finished subject 427
finished subject 428
finished subject 429
finished subject 430
finished subject 431
finished subject 432
finished subject 433
finished subject 434
finished subject 435
finished subject 436
finished subject 437
finished subject 438
finished subject 439
finished subject 440
finished subject 441
finished subject 442
finished subj

finished subject 787
finished subject 788
finished subject 789
finished subject 790
finished subject 791
finished subject 792
finished subject 793
finished subject 794
finished subject 795
finished subject 796
finished subject 797
finished subject 798
finished subject 799
finished subject 800
finished subject 801
finished subject 802
finished subject 803
finished subject 804
finished subject 805
finished subject 806
finished subject 807
finished subject 808
finished subject 809
finished subject 810
finished subject 811
finished subject 812
finished subject 813
finished subject 814
finished subject 815
finished subject 816
finished subject 817
finished subject 818
finished subject 819
finished subject 820
finished subject 821
finished subject 822
finished subject 823
finished subject 824
finished subject 825
finished subject 826
finished subject 827
finished subject 828
finished subject 829
finished subject 830
finished subject 831
finished subject 832
finished subject 833
finished subj

In [75]:
all_seed2voxel.shape

(91282, 992)

In [76]:
all_seed2voxel = pd.DataFrame(data=all_seed2voxel,    # values
...              columns=subjects_num)

all_seed2voxel = all_seed2voxel.T

In [77]:
all_seed2voxel

0         1         2         3         4         5         6      \
100206    1.0 -0.009217  0.008370  0.019375 -0.015024 -0.000942  0.019702   
209834    1.0  0.010916  0.036168  0.023514 -0.038584 -0.013273  0.000251   
209935    1.0 -0.000746 -0.018550 -0.005727  0.002515  0.009442  0.046840   
250932    1.0  0.013981  0.011119 -0.001029  0.013942  0.034884  0.035288   
214625    1.0 -0.021184  0.017422  0.012189  0.038041  0.045048  0.032212   
...       ...       ...       ...       ...       ...       ...       ...   
208327    1.0 -0.009598  0.005362  0.045730  0.021564  0.141682  0.073034   
208630    1.0  0.040619  0.047058  0.083904  0.123098 -0.013268  0.016133   
209127    1.0  0.056750 -0.012065 -0.003868  0.032678 -0.034007 -0.018433   
209228    1.0  0.000032  0.002474  0.019795  0.018302 -0.000337 -0.021752   
209329    1.0 -0.024305 -0.046277  0.014867 -0.032858 -0.019166  0.008300   

           7         8         9      ...     91272     91273     91274  \
100206  0.025033  0.070784  0.024707  ... -0.008185  0.007437 -0.007412   
209834 -0.026477  0.024600  0.026260  ...  0.016954  0.025345 -0.007092   
209935  0.030817  0.034181 -0.005495  ...  0.025867 -0.007902 -0.014025   
250932  0.011297  0.022193  0.026226  ...  0.003208  0.004484  0.004946   
214625  0.011276  0.100259  0.061415  ...  0.019688  0.033844  0.004167   
...          ...       ...       ...  ...       ...       ...       ...   
208327  0.022887  0.096844  0.005621  ...  0.030350 -0.000720  0.044320   
208630  0.080767  0.059703  0.068607  ... -0.027924 -0.041427 -0.002394   
209127 -0.014925  0.061243  0.005846  ...  0.011567  0.013243 -0.021055   
209228  0.016746  0.029719  0.017757  ...  0.011079  0.019622  0.011643   
209329 -0.012966  0.104134  0.004379  ...  0.019361 -0.013239  0.016826   

           91275     91276     91277     91278     91279     91280     91281  
100206  0.017128 -0.002044  0.020619  0.005389 -0.013439 -0.013599  0.008122  
209834 -0.018204  0.010947  0.015014  0.016419  0.011060 -0.012787  0.005642  
209935 -0.016598  0.016034 -0.021041 -0.023449 -0.017587 -0.007430  0.006656  
250932  0.024963 -0.018017 -0.039000  0.018589 -0.000500  0.016140  0.014189  
214625  0.031635 -0.000404 -0.004257  0.060127 -0.008965 -0.014972  0.033185  
...          ...       ...       ...       ...       ...       ...       ...  
208327  0.048731  0.000512  0.019538  0.013245 -0.022657 -0.015497  0.022808  
208630  0.020118 -0.022718  0.035600  0.043427  0.029767  0.035192  0.013121  
209127 -0.019163 -0.001153 -0.006448 -0.022727  0.001606  0.000391  0.000284  
209228  0.002590  0.030646  0.032764 -0.008585 -0.007136  0.005319  0.009850  
209329  0.035948  0.003553 -0.018343 -0.023269 -0.003316 -0.014500  0.002791  

[992 rows x 91282 columns]

In [78]:
#save df
all_seed2voxel.to_csv(conf.RESULTS_DIR + 'all_seed2voxel_visSeed.csv')

### Step 2: relate connectivity patterns to a behavioral trait

Load data

In [ ]:
#path_ROI_corr = conf.RESULTS_DIR + 'res_vmPFC_vis.csv'
path_seed2voxel = conf.RESULTS_DIR + 'all_seed2voxel_visSeed.csv'

#path to subject IDs 
path_sub = conf.BASE_DIR + conf.X_FEATURES_DIR + conf.SUB_ID_FILENAME

#path to behavioral data (analyzed in the analyze_behavior notebook)
path_behavior = conf.BASE_DIR + 'Behavior/HCP_behavior_includeZscores.csv'

all_seed2voxel_visSeed = pd.read_csv(path_seed2voxel)
subject_IDs = np.loadtxt(path_sub)
subject_IDs = subject_IDs.astype(int) #turn the subject IDS into integers
df_behav = pd.read_csv(path_behavior)
#df_behav

Equalize number of subjevts between df_behav and all_seed2voxel

In [88]:
all_seed2voxel_visSeed = all_seed2voxel_visSeed.rename(columns={'Unnamed: 0':'Subject'})
all_seed2voxel_visSeed

Subject    0         1         2         3         4         5         6  \
0     100206  1.0 -0.009217  0.008370  0.019375 -0.015024 -0.000942  0.019702   
1     209834  1.0  0.010916  0.036168  0.023514 -0.038584 -0.013273  0.000251   
2     209935  1.0 -0.000746 -0.018550 -0.005727  0.002515  0.009442  0.046840   
3     250932  1.0  0.013981  0.011119 -0.001029  0.013942  0.034884  0.035288   
4     214625  1.0 -0.021184  0.017422  0.012189  0.038041  0.045048  0.032212   
..       ...  ...       ...       ...       ...       ...       ...       ...   
987   208327  1.0 -0.009598  0.005362  0.045730  0.021564  0.141682  0.073034   
988   208630  1.0  0.040619  0.047058  0.083904  0.123098 -0.013268  0.016133   
989   209127  1.0  0.056750 -0.012065 -0.003868  0.032678 -0.034007 -0.018433   
990   209228  1.0  0.000032  0.002474  0.019795  0.018302 -0.000337 -0.021752   
991   209329  1.0 -0.024305 -0.046277  0.014867 -0.032858 -0.019166  0.008300   

            7         8  ...     91273     91274     91275     91276  \
0    0.025033  0.070784  ...  0.007437 -0.007412  0.017128 -0.002044   
1   -0.026477  0.024600  ...  0.025345 -0.007092 -0.018204  0.010947   
2    0.030817  0.034181  ... -0.007902 -0.014025 -0.016598  0.016034   
3    0.011297  0.022193  ...  0.004484  0.004946  0.024963 -0.018017   
4    0.011276  0.100259  ...  0.033844  0.004167  0.031635 -0.000404   
..        ...       ...  ...       ...       ...       ...       ...   
987  0.022887  0.096844  ... -0.000720  0.044320  0.048731  0.000512   
988  0.080767  0.059703  ... -0.041427 -0.002394  0.020118 -0.022718   
989 -0.014925  0.061243  ...  0.013243 -0.021055 -0.019163 -0.001153   
990  0.016746  0.029719  ...  0.019622  0.011643  0.002590  0.030646   
991 -0.012966  0.104134  ... -0.013239  0.016826  0.035948  0.003553   

        91277     91278     91279     91280     91281  Subject  
0    0.020619  0.005389 -0.013439 -0.013599  0.008122   100206  
1    0.015014  0.016419  0.011060 -0.012787  0.005642   209834  
2   -0.021041 -0.023449 -0.017587 -0.007430  0.006656   209935  
3   -0.039000  0.018589 -0.000500  0.016140  0.014189   250932  
4   -0.004257  0.060127 -0.008965 -0.014972  0.033185   214625  
..        ...       ...       ...       ...       ...      ...  
987  0.019538  0.013245 -0.022657 -0.015497  0.022808   208327  
988  0.035600  0.043427  0.029767  0.035192  0.013121   208630  
989 -0.006448 -0.022727  0.001606  0.000391  0.000284   209127  
990  0.032764 -0.008585 -0.007136  0.005319  0.009850   209228  
991 -0.018343 -0.023269 -0.003316 -0.014500  0.002791   209329  

[992 rows x 91284 columns]

In [84]:
df_behav = df_behav[df_behav['Subject'].isin(subject_IDs)]
df_behav.shape

(990, 590)

In [86]:
subjectBehavior = df_behav['Subject']
subjectDifference = np.setdiff1d(subject_IDs, subjectBehavior)
subjectDifference

array([314225, 392750])

In [87]:
all_seed2voxel_visSeed['Subject'] = subject_IDs
all_seed2voxel_visSeed

Unnamed: 0    0         1         2         3         4         5  \
0        100206  1.0 -0.009217  0.008370  0.019375 -0.015024 -0.000942   
1        209834  1.0  0.010916  0.036168  0.023514 -0.038584 -0.013273   
2        209935  1.0 -0.000746 -0.018550 -0.005727  0.002515  0.009442   
3        250932  1.0  0.013981  0.011119 -0.001029  0.013942  0.034884   
4        214625  1.0 -0.021184  0.017422  0.012189  0.038041  0.045048   
..          ...  ...       ...       ...       ...       ...       ...   
987      208327  1.0 -0.009598  0.005362  0.045730  0.021564  0.141682   
988      208630  1.0  0.040619  0.047058  0.083904  0.123098 -0.013268   
989      209127  1.0  0.056750 -0.012065 -0.003868  0.032678 -0.034007   
990      209228  1.0  0.000032  0.002474  0.019795  0.018302 -0.000337   
991      209329  1.0 -0.024305 -0.046277  0.014867 -0.032858 -0.019166   

            6         7         8  ...     91273     91274     91275  \
0    0.019702  0.025033  0.070784  ...  0.007437 -0.007412  0.017128   
1    0.000251 -0.026477  0.024600  ...  0.025345 -0.007092 -0.018204   
2    0.046840  0.030817  0.034181  ... -0.007902 -0.014025 -0.016598   
3    0.035288  0.011297  0.022193  ...  0.004484  0.004946  0.024963   
4    0.032212  0.011276  0.100259  ...  0.033844  0.004167  0.031635   
..        ...       ...       ...  ...       ...       ...       ...   
987  0.073034  0.022887  0.096844  ... -0.000720  0.044320  0.048731   
988  0.016133  0.080767  0.059703  ... -0.041427 -0.002394  0.020118   
989 -0.018433 -0.014925  0.061243  ...  0.013243 -0.021055 -0.019163   
990 -0.021752  0.016746  0.029719  ...  0.019622  0.011643  0.002590   
991  0.008300 -0.012966  0.104134  ... -0.013239  0.016826  0.035948   

        91276     91277     91278     91279     91280     91281  Subject  
0   -0.002044  0.020619  0.005389 -0.013439 -0.013599  0.008122   100206  
1    0.010947  0.015014  0.016419  0.011060 -0.012787  0.005642   209834  
2    0.016034 -0.021041 -0.023449 -0.017587 -0.007430  0.006656   209935  
3   -0.018017 -0.039000  0.018589 -0.000500  0.016140  0.014189   250932  
4   -0.000404 -0.004257  0.060127 -0.008965 -0.014972  0.033185   214625  
..        ...       ...       ...       ...       ...       ...      ...  
987  0.000512  0.019538  0.013245 -0.022657 -0.015497  0.022808   208327  
988 -0.022718  0.035600  0.043427  0.029767  0.035192  0.013121   208630  
989 -0.001153 -0.006448 -0.022727  0.001606  0.000391  0.000284   209127  
990  0.030646  0.032764 -0.008585 -0.007136  0.005319  0.009850   209228  
991  0.003553 -0.018343 -0.023269 -0.003316 -0.014500  0.002791   209329  

[992 rows x 91284 columns]

In [ ]:
all_seed2voxel_visSeed= all_seed2voxel_visSeed[(all_seed2voxel_visSeed.Subject != subjectDifference[0]) & (all_seed2voxel_visSeed.Subject != subjectDifference[1]) ]

Correalte between each column of the all_seed2voxel and the behavioral trait

In [63]:
#res = np.empty([1, num_v])
res = []
behav = df_behav["z_score_compare_f"]
for column in all_seed2voxel:
    res.append(pearsonr(all_seed2voxel[column], behav)[0])

100206    1.0
100307    1.0
Name: 0, dtype: float64
100206   -0.009217
100307    0.010100
Name: 1, dtype: float64
100206    0.008370
100307    0.043808
Name: 2, dtype: float64
100206    0.019375
100307    0.058775
Name: 3, dtype: float64
100206   -0.015024
100307   -0.022236
Name: 4, dtype: float64
100206   -0.000942
100307    0.005027
Name: 5, dtype: float64
100206    0.019702
100307   -0.024475
Name: 6, dtype: float64
100206    0.025033
100307    0.001843
Name: 7, dtype: float64
100206    0.070784
100307    0.106624
Name: 8, dtype: float64
100206    0.024707
100307    0.032347
Name: 9, dtype: float64
100206    0.038005
100307    0.015711
Name: 10, dtype: float64
100206    0.647319
100307    0.768998
Name: 11, dtype: float64
100206    0.220156
100307    0.372914
Name: 12, dtype: float64
100206    0.050816
100307    0.129586
Name: 13, dtype: float64
100206    0.031265
100307    0.063864
Name: 14, dtype: float64
100206    0.031258
100307    0.024152
Name: 15, dtype: float64
100206    0.

Name: 282, dtype: float64
100206    0.022705
100307    0.100529
Name: 283, dtype: float64
100206    0.049642
100307    0.108202
Name: 284, dtype: float64
100206    0.021532
100307    0.098946
Name: 285, dtype: float64
100206    0.006178
100307    0.069110
Name: 286, dtype: float64
100206    0.022838
100307    0.038763
Name: 287, dtype: float64
100206    0.025595
100307    0.030537
Name: 288, dtype: float64
100206    0.051796
100307    0.086017
Name: 289, dtype: float64
100206    0.036419
100307    0.067059
Name: 290, dtype: float64
100206    0.025352
100307    0.044170
Name: 291, dtype: float64
100206    0.032345
100307    0.039420
Name: 292, dtype: float64
100206    0.043605
100307    0.054484
Name: 293, dtype: float64
100206    0.045407
100307    0.077754
Name: 294, dtype: float64
100206    0.042904
100307    0.095237
Name: 295, dtype: float64
100206    0.054043
100307    0.102024
Name: 296, dtype: float64
100206    0.035260
100307    0.093732
Name: 297, dtype: float64
100206    0.01

Name: 541, dtype: float64
100206   -0.007814
100307    0.021724
Name: 542, dtype: float64
100206    0.007907
100307    0.009612
Name: 543, dtype: float64
100206    0.015995
100307    0.017772
Name: 544, dtype: float64
100206   -0.004213
100307    0.022613
Name: 545, dtype: float64
100206    0.007066
100307    0.014105
Name: 546, dtype: float64
100206    0.020622
100307    0.028458
Name: 547, dtype: float64
100206    0.018884
100307   -0.017541
Name: 548, dtype: float64
100206    0.014834
100307    0.018411
Name: 549, dtype: float64
100206    0.006610
100307    0.033512
Name: 550, dtype: float64
100206   -0.028027
100307    0.012601
Name: 551, dtype: float64
100206    0.002941
100307   -0.004482
Name: 552, dtype: float64
100206    0.011896
100307    0.014534
Name: 553, dtype: float64
100206   -0.016312
100307    0.008231
Name: 554, dtype: float64
100206    0.003505
100307    0.012703
Name: 555, dtype: float64
100206   -0.011523
100307   -0.034565
Name: 556, dtype: float64
100206    0.02

Name: 883, dtype: float64
100206    0.016628
100307   -0.013551
Name: 884, dtype: float64
100206   -0.010745
100307    0.012305
Name: 885, dtype: float64
100206   -0.005862
100307    0.055910
Name: 886, dtype: float64
100206    0.031899
100307    0.061611
Name: 887, dtype: float64
100206    0.049805
100307    0.066803
Name: 888, dtype: float64
100206    0.052122
100307    0.055857
Name: 889, dtype: float64
100206    0.048264
100307    0.050642
Name: 890, dtype: float64
100206    0.029037
100307    0.059939
Name: 891, dtype: float64
100206    0.031346
100307    0.089664
Name: 892, dtype: float64
100206    0.044283
100307    0.094868
Name: 893, dtype: float64
100206    0.029387
100307    0.019185
Name: 894, dtype: float64
100206    0.029613
100307    0.018065
Name: 895, dtype: float64
100206    0.035423
100307    0.018316
Name: 896, dtype: float64
100206    0.024167
100307    0.011142
Name: 897, dtype: float64
100206    0.015854
100307    0.000624
Name: 898, dtype: float64
100206    0.05

Name: 1215, dtype: float64
100206    0.014030
100307   -0.051024
Name: 1216, dtype: float64
100206    0.021693
100307   -0.035103
Name: 1217, dtype: float64
100206    0.011972
100307    0.023285
Name: 1218, dtype: float64
100206    0.010000
100307    0.057077
Name: 1219, dtype: float64
100206    0.009476
100307    0.060317
Name: 1220, dtype: float64
100206   -0.009309
100307    0.048240
Name: 1221, dtype: float64
100206   -0.013898
100307    0.019736
Name: 1222, dtype: float64
100206    0.017408
100307   -0.019106
Name: 1223, dtype: float64
100206   -0.004741
100307   -0.016238
Name: 1224, dtype: float64
100206   -0.009684
100307   -0.006805
Name: 1225, dtype: float64
100206   -0.003146
100307    0.006943
Name: 1226, dtype: float64
100206    0.017096
100307    0.024272
Name: 1227, dtype: float64
100206    0.030353
100307    0.045615
Name: 1228, dtype: float64
100206    0.030831
100307    0.062919
Name: 1229, dtype: float64
100206    0.041774
100307    0.070783
Name: 1230, dtype: float6

...

Name: 90558, dtype: float64
100206    0.009238
100307    0.032551
Name: 90559, dtype: float64
100206    0.036139
100307   -0.003058
Name: 90560, dtype: float64
100206   -0.010525
100307   -0.029878
Name: 90561, dtype: float64
100206    0.006977
100307   -0.038428
Name: 90562, dtype: float64
100206    0.035531
100307   -0.007821
Name: 90563, dtype: float64
100206    0.033750
100307   -0.002155
Name: 90564, dtype: float64
100206    0.033631
100307    0.024592
Name: 90565, dtype: float64
100206    0.019635
100307   -0.007169
Name: 90566, dtype: float64
100206    0.035114
100307   -0.029495
Name: 90567, dtype: float64
100206    0.001636
100307    0.011698
Name: 90568, dtype: float64
100206   -0.008700
100307    0.017172
Name: 90569, dtype: float64
100206   -0.010123
100307    0.030328
Name: 90570, dtype: float64
100206    0.001256
100307   -0.011992
Name: 90571, dtype: float64
100206    0.024613
100307   -0.032570
Name: 90572, dtype: float64
100206    0.016186
100307   -0.008365
Name: 9057

Name: 90722, dtype: float64
100206   -0.019733
100307   -0.000190
Name: 90723, dtype: float64
100206   -0.011225
100307    0.019616
Name: 90724, dtype: float64
100206   -0.020492
100307    0.013485
Name: 90725, dtype: float64
100206    0.002877
100307    0.025897
Name: 90726, dtype: float64
100206    0.008898
100307   -0.012762
Name: 90727, dtype: float64
100206    0.016361
100307   -0.002419
Name: 90728, dtype: float64
100206   -0.004109
100307    0.006857
Name: 90729, dtype: float64
100206   -0.015397
100307    0.007405
Name: 90730, dtype: float64
100206    0.001934
100307   -0.001365
Name: 90731, dtype: float64
100206    0.027087
100307    0.000844
Name: 90732, dtype: float64
100206    0.072961
100307   -0.014864
Name: 90733, dtype: float64
100206    0.032557
100307   -0.015694
Name: 90734, dtype: float64
100206    0.036083
100307   -0.029130
Name: 90735, dtype: float64
100206    0.038783
100307   -0.006127
Name: 90736, dtype: float64
100206   -0.012381
100307    0.004030
Name: 9073

Name: 90910, dtype: float64
100206   -0.020258
100307    0.003964
Name: 90911, dtype: float64
100206    0.004619
100307    0.008779
Name: 90912, dtype: float64
100206    0.011396
100307   -0.000675
Name: 90913, dtype: float64
100206    0.012891
100307   -0.009253
Name: 90914, dtype: float64
100206    0.025869
100307    0.008067
Name: 90915, dtype: float64
100206    0.011410
100307   -0.005222
Name: 90916, dtype: float64
100206   -0.014175
100307   -0.013680
Name: 90917, dtype: float64
100206   -0.006838
100307    0.010106
Name: 90918, dtype: float64
100206   -0.008863
100307    0.012064
Name: 90919, dtype: float64
100206   -0.010923
100307   -0.006297
Name: 90920, dtype: float64
100206    0.005781
100307   -0.011516
Name: 90921, dtype: float64
100206   -0.001550
100307   -0.017086
Name: 90922, dtype: float64
100206    0.000022
100307   -0.015748
Name: 90923, dtype: float64
100206    0.008252
100307    0.005726
Name: 90924, dtype: float64
100206    0.007579
100307   -0.011395
Name: 9092

Name: 91075, dtype: float64
100206    0.000721
100307    0.000628
Name: 91076, dtype: float64
100206   -0.008492
100307    0.002221
Name: 91077, dtype: float64
100206    0.024892
100307    0.025421
Name: 91078, dtype: float64
100206    0.005704
100307    0.018388
Name: 91079, dtype: float64
100206   -0.019317
100307    0.007419
Name: 91080, dtype: float64
100206   -0.011770
100307    0.005366
Name: 91081, dtype: float64
100206    0.014948
100307    0.023488
Name: 91082, dtype: float64
100206    0.005694
100307    0.035331
Name: 91083, dtype: float64
100206   -0.014238
100307    0.007327
Name: 91084, dtype: float64
100206   -0.022299
100307    0.008056
Name: 91085, dtype: float64
100206    0.016841
100307    0.014836
Name: 91086, dtype: float64
100206    0.011100
100307    0.025803
Name: 91087, dtype: float64
100206   -0.013112
100307    0.006161
Name: 91088, dtype: float64
100206    0.018414
100307   -0.004307
Name: 91089, dtype: float64
100206    0.061089
100307    0.013623
Name: 9109

Name: 91270, dtype: float64
100206    0.008687
100307    0.015024
Name: 91271, dtype: float64
100206   -0.008185
100307    0.004358
Name: 91272, dtype: float64
100206    0.007437
100307    0.005909
Name: 91273, dtype: float64
100206   -0.007412
100307    0.007618
Name: 91274, dtype: float64
100206    0.017128
100307    0.007024
Name: 91275, dtype: float64
100206   -0.002044
100307    0.013779
Name: 91276, dtype: float64
100206    0.020619
100307    0.011440
Name: 91277, dtype: float64
100206    0.005389
100307   -0.002916
Name: 91278, dtype: float64
100206   -0.013439
100307    0.022243
Name: 91279, dtype: float64
100206   -0.013599
100307    0.025279
Name: 91280, dtype: float64
100206    0.008122
100307   -0.002256
Name: 91281, dtype: float64
